In [56]:
import numpy as np
import scipy.signal as sg
import matplotlib.pyplot as plt
import cmocean

import librosa

import soundfile as sf

from plotly.subplots import make_subplots
import plotly.graph_objects as go
import plotly.express as px

In [155]:

#sample_name = "001328dc-ea5d-4847-9ccf-c5aa2a3f2d0f.webm.flac"
#sample_name = "no-detectable_train_id_1171_audio_2020-10-18_at_14_09_27.290.ogg.flac"
#sample_name = "NEPS_COVID_TOS_d13eb2fb-057a-4764-a894-7147cc4f28ce.wav.flac"
sample_name = "NEPS_COVID_TOS_d14db2be-5516-4342-8389-0811da1ea0c6.wav.flac"
#sample_name = "NEPS_COVID_TOS_d17fdbf2-ff3c-4655-8dac-7f7f37c57672.wav.flac"
#sample_name = "NEPS_COVID_TOS_ef53726b-d86b-4634-92f7-6a04423d3868.wav.flac"
#sample_name = "NEPS_COVID_TOS_ef71222d-4f95-4750-837c-bff6c64a1545.wav.flac"
#sample_name = "NEPS_COVID_TOS_ef73352c-0ef8-477d-acd9-3de1d4498aa6.wav.flac")

my_data, my_samplerate = sf.read("../samples/" + sample_name)

spec = librosa.stft(y = my_data, n_fft = 511, hop_length = 128, window='hann')

spec_mag = abs(spec) # real numbers (magnitude)
spec_sqrd = spec**2  # complex numbers 

spec_zeroed = np.where(spec_sqrd < 0, 0, spec_mag)

#_, ax = plt.subplots(figsize=(10, 10))
#ax.pcolormesh(np.log10(spec_mag), cmap=cmocean.cm.ice)
px.imshow(np.log10(spec_mag), origin='lower').show()

np.set_printoptions(precision=3)
print(spec)


[[-2.221e-01+0.000e+00j -3.433e-01+0.000e+00j -2.362e-01+0.000e+00j ...
   5.870e-01+0.000e+00j  3.887e-01+0.000e+00j  2.712e-01+0.000e+00j]
 [ 1.177e-01-1.468e-01j  2.254e-01+2.796e-02j  1.198e-01+8.012e-02j ...
  -3.384e-01-9.768e-02j -1.528e-01-9.674e-02j -1.538e-01-1.151e-02j]
 [ 1.104e-02+1.139e-01j -5.177e-02-7.301e-02j -2.047e-02+6.093e-03j ...
   4.814e-02+4.947e-02j -5.034e-02+4.107e-02j  1.696e-02-4.943e-02j]
 ...
 [ 1.452e-04-9.230e-05j -7.265e-05+1.346e-04j  6.081e-05+1.392e-05j ...
   8.205e-05+6.584e-07j -3.598e-05+6.794e-05j -1.576e-03+1.602e-03j]
 [-7.049e-05+1.686e-04j  1.800e-04-9.617e-05j -1.273e-04-2.394e-05j ...
  -8.616e-05+3.562e-05j  3.592e-05+2.080e-05j -1.609e-03-1.544e-03j]
 [ 2.098e-06-1.428e-04j -9.171e-05+1.676e-05j  5.917e-05+5.092e-05j ...
   3.912e-05-6.718e-05j -7.119e-07-1.147e-04j  1.586e-03-1.699e-03j]]


In [159]:


# Rank computation
from webbrowser import BackgroundBrowser


tol = 0.5
def gen_rank_matrix(data, conv_size=7):
    C, R = data.shape
    rank_matrix = np.zeros((C - conv_size, R - conv_size))
    for c in range(0, C - conv_size):
        for r in range(0, R - conv_size):
            conv_arr = data[c:c+conv_size,
                            r:r+conv_size]
            rank_matrix[c, r] = np.linalg.matrix_rank(conv_arr, tol) 
    return rank_matrix

rank_spec_mag = gen_rank_matrix(spec_mag)
rank_spec_zeroed = gen_rank_matrix(spec_zeroed)

fig = make_subplots(rows=2, cols=1, subplot_titles=(
                                                    "Ranks of magnitude spectrogram using 7x7 sub-array (tolerance = 0.001),", 
                                                    "Ranks of zeroed spectrogram using 7x7 sub-array",
                                                    ))
fig.update_layout(height=600, title_text="Tolerance=%s, sample_name=%s" % (tol, sample_name))

fig.append_trace(
    px.imshow(rank_spec_mag).data[0],
    row=1, col=1
)
fig.append_trace(
    px.imshow(rank_spec_zeroed).data[0],
    row=2, col=1
)

fig.show()
px.imshow(np.log10(spec_mag), origin='lower', title=f'Spectrogram: log10(spec_mag)<br><sup>{sample_name}</sup>').show()

px.imshow(rank_spec_zeroed - rank_spec_mag, origin='lower', 
    title="RankZeroed minus RankMagnitude<br>\
           <sup>Consturct rank matrix for Magnitude and Zeroed spectrograms by calc rank of each 7x7 subarray</sup><br>\
           <sup>SVD Tolerance=%s, sample_name=%s</sup>" % (tol, sample_name)).show()